In [ ]:
import pandas as pd
from pybedtools import BedTool

# 查看ATAC-seq在目标位置的信号变化

## 准备df

### df_ctcf
- weak
- medium
- strong
- overlapped with offs

In [ ]:
df_new_offs = pd.read_csv(
    '/lustre1/chengqiyi_pkuhpc/zhaohn/3.project/2022_DdCBE-3D-Genome_topic/'
    '2022-09-30_Detect-seq_batch-1_ATP8_JAK2_SIRT6/final_list_after_igv_check/'
    '2023-04-24_merged_final_list_add_header_poisson_result.csv',
    header=0,
)
df_new_offs = df_new_offs[['chr_name', 'region_start', 'region_end']].copy()
df_new_offs.columns = ['chrom', 'start', 'end']
df_new_offs.drop_duplicates(keep='first', inplace=True)
df_new_offs

In [ ]:
df_old_offs = pd.read_csv(
    '/lustre1/chengqiyi_pkuhpc/zhaohn/3.project/2022_DdCBE-3D-Genome_topic/'
    '2022-09-30_Detect-seq_batch-1_ATP8_JAK2_SIRT6/tables/'
    '2022-10-05_WT_ND4-5.1-6_final-list.bed',
    header=None, sep='\t', names=['chrom', 'start', 'end', 'name', 'score', 'strand']
)
df_old_offs = df_old_offs.query('name.str.contains("IND")').copy()
df_old_offs

In [ ]:
df_offs = pd.concat(
    [
        df_old_offs.iloc[:,:3],
        df_new_offs.iloc[:,:3]
    ]
)
df_offs

In [ ]:
df_ctcf = pd.read_csv('/lustre1/chengqiyi_pkuhpc/zhaohn/1.database/public_data/CTCF_ATAC_data/ENCFF285QVL_CTCF_binding_sites_fix_range.bed',
                     sep='\t')
df_ctcf

In [ ]:
a = BedTool.from_dataframe(df_offs.iloc[:,:3])
b = BedTool.from_dataframe(df_ctcf.iloc[:,:3])
# 去掉在off里的ctcf
df_ctcf_out_offs = b.intersect(a, loj=True).to_dataframe().query('score==-1').iloc[:, :3].merge(df_ctcf, on=['chrom', 'start', 'end'], how='left')
df_ctcf_in_offs = b.intersect(a, loj=True).to_dataframe().query('score!=-1').iloc[:, :3].merge(df_ctcf, on=['chrom', 'start', 'end'], how='left')
df_ctcf_out_offs

In [ ]:
df_ctcf_out_offs['signal_strength'] = df_ctcf_out_offs['name'].str.split('_').str[-2]
df_ctcf_out_offs

In [ ]:
df_ctcf_in_offs['signal_strength'] = df_ctcf_in_offs['name'].str.split('_').str[-2]
df_ctcf_in_offs

In [ ]:
df_ctcf_out_offs.signal_strength.value_counts()

In [ ]:
df_ctcf_in_offs.signal_strength.value_counts()

In [ ]:
36565 / (110 + 107 + 36565) * 1580

# 所以从CTCF强度上看不出有无offtarget的差别

In [ ]:
for signal, df in df_ctcf_out_offs.groupby('signal_strength'):
    # print(signal)
    # print(df.drop(columns='signal_strength'))
    df.drop(columns='signal_strength').to_csv(f'../bed_for_count/2023-05-12_CTCF_{signal}_for_count.bed', header=False, index=False, sep='\t')

In [ ]:
df_ctcf_in_offs.drop(columns='signal_strength').to_csv(f'../bed_for_count/2023-05-12_CTCF_within-offs_for_count.bed', header=False, index=False, sep='\t')

### df_offs

In [ ]:
df_offs = pd.read_csv(
    '/lustre1/chengqiyi_pkuhpc/zhaohn/3.project/2022_DdCBE-3D-Genome_topic/'
    '2022-09-30_Detect-seq_batch-1_ATP8_JAK2_SIRT6/tables/'
    '2022-10-05_WT_ND4-5.1-6_final-list.bed',
    header=None, sep='\t', names=['chrom', 'start', 'end', 'name', 'score', 'strand']
)
df_offs

In [ ]:
df_offs_IND = pd.concat(
    [
        # df_offs.query('name.str.contains("ND6-TAS.DL")'),
        # df_offs.query('name.str.contains("ND6-TAS.DR")'),
        df_offs.query('name.str.contains("ND6-TAS.IND")')
    ]
)
df_offs_IND

In [ ]:
df_offs_DEP = pd.concat(
    [
        df_offs.query('name.str.contains("ND6-TAS.DL")'),
        df_offs.query('name.str.contains("ND6-TAS.DR")'),
        # df_offs.query('name.str.contains("ND6-TAS.IND")')
    ]
)
df_offs_DEP

In [ ]:
df_offs_IND.to_csv(f'../bed_for_count/2023-05-12_offs-ND6-IND_for_count.bed', header=False, index=False, sep='\t')
df_offs_DEP.to_csv(f'../bed_for_count/2023-05-12_offs-ND6-DEP_for_count.bed', header=False, index=False, sep='\t')

### df_random

In [ ]:
random = BedTool().random(l=200, n=33000, genome='hg38', seed=123)
print(random.to_dataframe())
random_fa = random.sequence(fi='/lustre1/chengqiyi_pkuhpc/zhaohn/1.database/db_genomes/genome_fa/genome_ucsc_hg38/genome_ucsc_hg38.fa')
df_random = pd.DataFrame(random_fa.print_sequence().split('>')[1:], columns=['info'])
df_random[['coordinate', 'sequence']] = df_random['info'].str.strip().str.split('\n', expand=True)
df_random = df_random.query('~sequence.str.upper().str.contains("N")').copy()
df_random

In [ ]:
df_random[['chrom', 'start', 'end']] = df_random['coordinate'].str.replace(':', '\t').str.replace('-', '\t').str.split('\t', expand=True)
df_random[['start', 'end']] = df_random[['start', 'end']].astype(int)
df_random

In [ ]:
df_random = df_random.merge(random.to_dataframe(), on=['chrom', 'start', 'end'], how='left')
df_random

In [ ]:
df_random = df_random[['chrom', 'start', 'end', 'name', 'score', 'strand']].copy()
df_random

In [ ]:
# rm overlapped with df_ctcf, df_offs
a = BedTool.from_dataframe(df_ctcf.iloc[:,:3])
b = BedTool.from_dataframe(df_random.iloc[:,:3])
df_random = b.intersect(a, loj=True).to_dataframe().query('score==-1').iloc[:, :3].merge(df_random, on=['chrom', 'start', 'end'], how='left')



df_offs = pd.concat(
    [
        df_old_offs.iloc[:,:3],
        df_new_offs.iloc[:,:3]
    ]
)
# df_offs



a = BedTool.from_dataframe(df_offs.iloc[:,:3])
b = BedTool.from_dataframe(df_random.iloc[:,:3])
df_random = b.intersect(a, loj=True).to_dataframe().query('score==-1').iloc[:, :3].merge(df_random, on=['chrom', 'start', 'end'], how='left')


df_random

In [ ]:
df_random.to_csv(f'../bed_for_count/2023-05-12_random_for_count.bed', header=False, index=False, sep='\t')

### df_tss

In [ ]:
df_tss = pd.read_csv('ref_data/hg38_ucsc_refseq_NM_TSS_extend2kb.sorted.bed', sep='\t', header=None,
                    names=['chrom', 'start', 'end', 'name', 'score', 'strand'])
df_tss

In [ ]:
# rm overlapped with df_offs
df_offs = pd.concat(
    [
        df_old_offs.iloc[:,:3],
        df_new_offs.iloc[:,:3]
    ]
)
# df_offs
a = BedTool.from_dataframe(df_offs.iloc[:,:3])
b = BedTool.from_dataframe(df_tss.iloc[:,:3])
df_tss = b.intersect(a, loj=True).to_dataframe().query('score==-1').iloc[:, :3].merge(df_tss, on=['chrom', 'start', 'end'], how='left')
df_tss

In [ ]:
# with df_ctcf, without, df_ctcf
a = BedTool.from_dataframe(df_ctcf.iloc[:,:3])
b = BedTool.from_dataframe(df_tss.iloc[:,:3])
df_tss_has_ctcf = b.intersect(a, loj=True).to_dataframe().query('score!=-1').iloc[:, :3].merge(df_tss, on=['chrom', 'start', 'end'], how='left')
df_tss_no_ctcf = b.intersect(a, loj=True).to_dataframe().query('score==-1').iloc[:, :3].merge(df_tss, on=['chrom', 'start', 'end'], how='left')

In [ ]:
df_tss_has_ctcf = df_tss_has_ctcf.drop_duplicates(keep='first')
df_tss_has_ctcf

In [ ]:
df_tss_no_ctcf = df_tss_no_ctcf.drop_duplicates(keep='first')
df_tss_no_ctcf

In [ ]:
df_tss_has_ctcf.to_csv(f'../bed_for_count/2023-05-12_tss_has_ctcf_for_count.bed', header=False, index=False, sep='\t')
df_tss_no_ctcf.to_csv(f'../bed_for_count/2023-05-12_tss_no_ctcf_for_count.bed', header=False, index=False, sep='\t')

## 准备count-table

In [ ]:
from glob import glob

In [ ]:
ls_bam = sorted(glob('../bam/ATACSeq_*.sortp_genome_rmchrM_rmdup.bam'))
bams = [i.split('Seq_')[-1].split('.sortp')[0] for i in ls_bam]
ls_bed = sorted(glob('../bed_for_count/*.bed'))
beds = [i.split('2023-05-12_')[-1].split('_for_count')[0] for i in ls_bed]
print(bams)
print(beds)

In [ ]:
# # run snakemake

## 分析比较ATAC-seq数据变化

### 使用DESeq2比较差异

In [ ]:
from glob import glob
import pandas as pd

In [ ]:
ls_counts = sorted(glob('../bed_for_count/AnalysisChanges_*.count_table'))
ls_counts

In [ ]:
df = pd.DataFrame(ls_counts, columns=['file_path'])
# df

In [ ]:
df['sample'] = df.file_path.str.split('BAM_').str[-1].str.split('_BED').str[0]
df['region'] = df.file_path.str.split('BED_').str[-1].str.split('.count').str[0]
df.head()

In [ ]:
samples = sorted(df['sample'].unique())
regions = sorted(df['region'].unique())
print(regions)
print(samples)

In [ ]:
df_total_reads = pd.read_csv('2023-05-12_step.03.MappingQC_result.csv', index_col=0).reset_index()
df_total_reads = df_total_reads[['index', 'map to genome remove duplicates (M)']].copy()
df_total_reads.columns = ['sample', 'total_reads_M']
df_total_reads = df_total_reads.query('sample!="test"').copy()
df_total_reads

In [ ]:
ls = []
for idx, line in df.iterrows():
    file_path, sample, region = line
    # print(file_path, sample, region)
    tmpdf = pd.read_csv(file_path, sep='\t', header=None)
    tmpdf['sample'] = sample
    tmpdf['region'] = region
    ls.append(tmpdf)
df_counts = pd.concat(ls)
df_counts.columns = ['chrom', 'start', 'end', 'name', 'score', 'strand', 'depth', '_1', '_2', '_3', 'sample', 'region']
df_counts = df_counts[['sample', 'region', 'chrom', 'start', 'end', 'name', 'score', 'strand', 'depth']].copy()
df_counts

In [ ]:
df_total_reads

In [ ]:
df_counts = df_counts.merge(df_total_reads, on='sample', how='left')
df_counts

In [ ]:
df_counts['region_length'] = df_counts['end'] -  df_counts['start']
df_counts['RPKM'] = df_counts['depth'] / (df_counts['region_length']/1_000 * df_counts['total_reads_M'])
df_counts['region_index'] = df_counts['chrom'] + '_' + df_counts['start'].astype(str) + '_' + df_counts['end'].astype(str)
df_counts.drop_duplicates(subset=['sample', 'region', 'region_index'], keep='first', inplace=True)
df_counts.set_index(['region_index', 'region'], inplace=True)
df_counts

In [ ]:
df_counts.RPKM.describe()

In [ ]:
df_counts

In [ ]:
# import itertools as it
# import math
# from lets_plot import *
# LetsPlot.setup_html()

In [ ]:
# ls = []
# for sample_2 in it.combinations(samples, 2):
#     s1, s2 = sample_2
#     s_s1 = df_counts.query('sample==@s1')[['RPKM', 'depth']]
#     s_s2 = df_counts.query('sample==@s2')[['RPKM', 'depth']]
#     df_sample_2 = pd.concat([s_s1, s_s2], axis=1)
#     df_sample_2.columns = ['RPKM1', 'count1', 'RPKM2', 'count2']
#     # df_sample_2 = df_sample_2[(df_sample_2.RPKM1 >= 0.5) & (df_sample_2.RPKM2 >= 0.5)].copy()
#     df_sample_2['Log2_FC_RPKM'] = (df_sample_2['RPKM1'] / df_sample_2['RPKM2']).map(math.log10)
#     df_sample_2['Geometric_mean'] = df_sample_2['RPKM1'].map(math.sqrt) * df_sample_2['RPKM2'].map(math.sqrt)
#     df_sample_2 = df_sample_2[['Log2_FC_RPKM', 'Geometric_mean', 'RPKM1', 'RPKM2', 'count1', 'count2']].reset_index().copy()
#     df_sample_2['compare'] = f'{s1} v.s. {s2}'
#     ls.append(df_sample_2)
# df_plot = pd.concat(ls)
# df_plot

In [ ]:
# print(df_plot.groupby(['compare', 'region']).region_index.count().to_frame().reset_index().to_string())

In [ ]:
# df_plot.groupby('compare').Log2_FC_RPKM.describe()

In [ ]:
# df_plot

In [ ]:
# g = (
#     ggplot(data=df_plot, mapping=aes(x='Log2_FC_RPKM', y='Geometric_mean'))
#     + geom_point()
#     + geom_line(x=0, color='red')
#     + facet_grid(x='compare', y='region', scales='free')
#     + ggsize(width=5500, height=1500)
#     + theme_minimal()
# )
# # g

In [ ]:
# ggsave(g, filename='2023-05-12_ATAC-seq_LogFC_compare.html', path='.', iframe=True)

In [ ]:
import pandas as pd
import itertools as it

In [ ]:
clinical_df = df_counts.reset_index()[['sample']].drop_duplicates(ignore_index=True)
clinical_df.index = clinical_df['sample']
clinical_df['treatment'] = clinical_df['sample'].str.split('_REP-').str[0]
clinical_df.columns = ['condition', 'group']
clinical_df.index = clinical_df.index.str.replace('-', '_')
clinical_df['condition'] = clinical_df['condition'].str.replace('-', '_')
clinical_df

In [ ]:
# depth or RPKM from here

df_feature = df_counts[['sample', 'depth']].reset_index()

df_feature.index = df_feature['sample']
df_feature['depth'] = df_feature['depth'].astype(int)
df_feature['gene'] = df_feature['region_index']
df_feature.index = df_feature.index.str.replace('-', '_')
df_feature['sample'] = df_feature['sample'].str.replace('-', '_')
# df_feature = df_feature.query('RPKM>0')
df_feature.index.name = 'index'
df_feature

In [ ]:
df_feature.groupby(['sample', 'region']).region_index.count()

In [ ]:
conditions = []
for region in df_feature.region.unique():
    for sample_2 in it.combinations(df_feature['sample'].unique(), 2):
        conditions.append([region, sample_2])
conditions

In [ ]:
# %load_ext autoreload
# %autoreload 3
import sys
sys.path.insert(0, "/lustre1/chengqiyi_pkuhpc/zhaohn/3.project/2022_DdCBE-3D-Genome_topic/2023-04-25_ATAC-seq/PyDESeq2")
import pydeseq2
print(f'pydeseq2 path: {pydeseq2.__path__}')


from pydeseq2.dds import DeseqDataSet
from pydeseq2.ds import DeseqStats


dt = {}

In [ ]:
for region, sample_2 in conditions:
    # print(region, sample_2)
    key = f"{region}:{sample_2[0]}_vs_{sample_2[1]}"

    if key in dt:
        # print('already exist, continue')
        continue

    counts_df = df_feature.query('region==@region').query('sample in @sample_2').copy()
    counts_df = counts_df.pivot_table(
        values='depth',
        index='sample',
        columns='gene',
        fill_value=0
    )

    counts_df.replace({0: 1}, inplace=True)
    # genes_to_keep = counts_df.columns[counts_df.sum(axis=0) >= 20]
    # counts_df = counts_df[genes_to_keep].copy()
    dds = DeseqDataSet(
        counts=counts_df,
        clinical=clinical_df.query('condition in @sample_2').copy(),
        design_factors='condition',
        refit_cooks=True,
        n_cpus=8,
    )
    # 使用中位数法计算DESeq2归一化因子
    # dds.fit_size_factors(fit_type='iterative')
    dds.fit_size_factors(fit_type='ratio')
    print("size_factors = ", dds.obsm["size_factors"])

    # 拟合每个基因的独立负二项模型
    dds.fit_genewise_dispersions()      # 问题出在这儿！！！！！！！！！！！！！！！！！！！！！！！！！！！！# 更新到github最新代码后就没问题了
    print("genewise_dispersions = ", dds.varm["genewise_dispersions"])
    print('*' * 100)
    # 拟合散度的参数化趋势曲线，形式为f(\mu) = \alpha_1/\mu + a_0
    dds.fit_dispersion_trend()
    # print("trend_coeffs = ", dds.uns["trend_coeffs"])
    # print("fitted_dispersions = ", dds.varm["fitted_dispersions"])
    # print('*' * 100)
    # 计算先验离散方差
    dds.fit_dispersion_prior()
    # print(f"logres_prior={dds.uns['_squared_logres']}, sigma_prior={dds.uns['prior_disp_var']}")
    # 调整基因离散后验(向趋势曲线收缩估计)
    dds.fit_MAP_dispersions()
    # print(dds.varm["MAP_dispersions"], dds.varm["dispersions"])
    # Fit log-fold changes (in natural log scale)
    dds.fit_LFC()
    # print(dds.varm["LFC"])
    # 计算库克距离以找到异常值
    dds.calculate_cooks()

    # 替换异常值计数，并重新定义被替换异常值的基因的离散度和lfc
    if dds.refit_cooks:
        dds.refit()

    stat_res = DeseqStats(dds, contrast=["condition", sample_2[0], sample_2[1]], n_cpus=8)  # ['variable_of_interest', 'tested_level', 'ref_level']
    stat_res.run_wald_test()
    # print(stat_res.p_values)

    if stat_res.cooks_filter:
        stat_res._cooks_filtering()
    # print(stat_res.p_values)
    if stat_res.independent_filter:
        stat_res._independent_filtering()
    else:
        stat_res._p_value_adjustment()

    # print(stat_res.padj)
    stat_res.summary()
    out_df1 = stat_res.results_df
    stat_res.lfc_shrink(coeff=f"condition_{sample_2[1]}_vs_{sample_2[0]}")
    out_df2 = stat_res.results_df
    out_df = pd.concat([out_df1, out_df2], axis=1)
    out_df['region'] = region
    out_df['compare'] = f'log2({sample_2[0]}/{sample_2[1]})'

    dt[key] = out_df
    del out_df, stat_res
print('Done')

In [ ]:
ls = [v for k, v in dt.items()]
df_plot_adj = pd.concat(ls)
df_plot_adj.columns = [
    'baseMean', 'log2FoldChange', 'lfcSE', 'stat', 'pvalue', 'padj',
    'baseMean_lfc_shrink', 'log2FoldChange_lfc_shrink', 'lfcSE_lfc_shrink', 'stat_lfc_shrink', 'pvalue_lfc_shrink', 'padj_lfc_shrink',
    "region", 'compare'
]
df_plot_adj

In [ ]:
pd.DataFrame(df_plot_adj['compare'].unique())

In [ ]:
df_plot_adj = (
    df_plot_adj
    .query('log2FoldChange.notna()')
    .query('baseMean>=3')
    .query('padj.notna()')
)

In [ ]:
df_plot_adj.fillna(0, inplace=True)
df_plot_adj

In [ ]:
df_plot_adj.to_csv('2023-05-25_DESeq2_results.csv.gz')

### 分析得到的差异数据

In [3]:
import math
import numpy as np
import pandas as pd

In [4]:
df_plot_adj = pd.read_csv('2023-05-25_DESeq2_results.csv.gz', index_col=0)

df_plot_adj.head()

baseMean  log2FoldChange     lfcSE      stat  \
gene                                                                        
chr10_100009417_100009841   86.369930       -0.186336  0.204236  1.324120   
chr10_100019785_100020209   12.739452       -0.144270  0.397130 -1.879785   
chr10_100185238_100185662  114.076004       -0.144270  0.397130  1.524337   
chr10_100338433_100338857   58.530212       -0.144270  0.397130  0.437214   
chr10_100347794_100348218   79.866570       -0.158916  0.206087  1.146350   

                             pvalue      padj  baseMean_lfc_shrink  \
gene                                                                 
chr10_100009417_100009841  0.185463  0.433983            86.369930   
chr10_100019785_100020209  0.060137  0.236292            12.739452   
chr10_100185238_100185662  0.127425  0.355752           114.076004   
chr10_100338433_100338857  0.661956  0.830464            58.530212   
chr10_100347794_100348218  0.251650  0.514463            79.866570   

                           log2FoldChange_lfc_shrink  lfcSE_lfc_shrink  \
gene                                                                     
chr10_100009417_100009841                  -0.186336          0.204236   
chr10_100019785_100020209                  -0.144270          0.397130   
chr10_100185238_100185662                  -0.144270          0.397130   
chr10_100338433_100338857                  -0.144270          0.397130   
chr10_100347794_100348218                  -0.158916          0.206087   

                           stat_lfc_shrink  pvalue_lfc_shrink  \
gene                                                            
chr10_100009417_100009841         1.324120           0.185463   
chr10_100019785_100020209        -1.879785           0.060137   
chr10_100185238_100185662         1.524337           0.127425   
chr10_100338433_100338857         0.437214           0.661956   
chr10_100347794_100348218         1.146350           0.251650   

                           padj_lfc_shrink       region  \
gene                                                      
chr10_100009417_100009841         0.433983  CTCF_medium   
chr10_100019785_100020209         0.236292  CTCF_medium   
chr10_100185238_100185662         0.355752  CTCF_medium   
chr10_100338433_100338857         0.830464  CTCF_medium   
chr10_100347794_100348218         0.514463  CTCF_medium   

                                                 compare  
gene                                                      
chr10_100009417_100009841  log2(GFP_NLS_REP_1/GFP_REP_1)  
chr10_100019785_100020209  log2(GFP_NLS_REP_1/GFP_REP_1)  
chr10_100185238_100185662  log2(GFP_NLS_REP_1/GFP_REP_1)  
chr10_100338433_100338857  log2(GFP_NLS_REP_1/GFP_REP_1)  
chr10_100347794_100348218  log2(GFP_NLS_REP_1/GFP_REP_1)

In [5]:
df_plot_adj.describe()

baseMean  log2FoldChange          lfcSE          stat  \
count  982008.000000   982008.000000  982008.000000  9.820080e+05   
mean      106.954568       -0.121662       0.451439  9.253873e-02   
std       133.681288        0.158923       0.261740  1.886261e+00   
min         3.000000       -3.772007       0.001429 -1.080495e+01   
25%        23.366718       -0.144270       0.379600 -1.146430e+00   
50%        51.000000       -0.144270       0.410867 -4.901255e-07   
75%       136.781127       -0.144270       0.472993  1.209947e+00   
max      2887.205600        4.024548       3.161517  1.599347e+01   

             pvalue          padj  baseMean_lfc_shrink  \
count  9.820080e+05  9.820080e+05        982008.000000   
mean   3.303062e-01  5.212485e-01           106.954568   
std    3.087488e-01  3.410451e-01           133.681288   
min    1.419005e-57  2.133899e-53             3.000000   
25%    4.622071e-02  1.933519e-01            23.366718   
50%    2.386456e-01  5.486346e-01            51.000000   
75%    5.694054e-01  8.597301e-01           136.781127   
max    1.000000e+00  1.000000e+00          2887.205600   

       log2FoldChange_lfc_shrink  lfcSE_lfc_shrink  stat_lfc_shrink  \
count              982008.000000     982008.000000     9.820080e+05   
mean                   -0.121662          0.451439     9.253873e-02   
std                     0.158923          0.261740     1.886261e+00   
min                    -3.772007          0.001429    -1.080495e+01   
25%                    -0.144270          0.379600    -1.146430e+00   
50%                    -0.144270          0.410867    -4.901255e-07   
75%                    -0.144270          0.472993     1.209947e+00   
max                     4.024548          3.161517     1.599347e+01   

       pvalue_lfc_shrink  padj_lfc_shrink  
count       9.820080e+05     9.820080e+05  
mean        3.303062e-01     5.212485e-01  
std         3.087488e-01     3.410451e-01  
min         1.419005e-57     2.133899e-53  
25%         4.622071e-02     1.933519e-01  
50%         2.386456e-01     5.486346e-01  
75%         5.694054e-01     8.597301e-01  
max         1.000000e+00     1.000000e+00

In [6]:
df_plot_adj.log2FoldChange.abs().describe()

count    9.820080e+05
mean     1.569272e-01
std      1.242254e-01
min      6.504978e-09
25%      1.442695e-01
50%      1.442695e-01
75%      1.442695e-01
max      4.024548e+00
Name: log2FoldChange, dtype: float64

In [7]:
df_plot_adj.log2FoldChange.abs().quantile(0.99)

0.728848360090406

In [8]:
math.pow(2, 0.1442695040888963)

1.1051709180756475

In [9]:
math.log2(1.11)

0.1505596765753814

In [10]:
# fc_mt = -math.log2(2)
# fc_lt = math.log2(2)
fc_mt = -1
fc_lt = 1
FDR = 0.05

In [11]:
def expresesion(x):
    if x['baseMean'] > 25:
        if (x['log2FoldChange'] >= fc_lt) and (x['padj'] <= FDR):
            return 'Up-regulated'
        elif (x['log2FoldChange'] <= fc_mt) and (x['padj'] <= FDR):
            return 'Down-regulated'
        else:
            return 'Unchanged'
    else:
        return np.NaN

df_plot_adj['expression'] = df_plot_adj.apply(expresesion, axis=1)
df_plot_adj_filter = df_plot_adj.dropna(axis=0).copy()
print(df_plot_adj_filter.expression.value_counts())
df_plot_adj_filter.baseMean.describe()

Unchanged         714871
Up-regulated        1097
Down-regulated       966
Name: expression, dtype: int64


count    716934.000000
mean        141.727992
std         141.347988
min          25.000126
25%          44.000000
50%          81.173050
75%         198.173000
max        2887.205600
Name: baseMean, dtype: float64

In [17]:
df_plot_adj_filter.query('region=="offs-ND6-IND"').expression.value_counts()

Unchanged         154
Down-regulated      6
Up-regulated        2
Name: expression, dtype: int64

In [12]:
df_plot_adj_filter = pd.concat(
    [
        # df_plot_adj_filter.query('expression=="Unchanged"'),
        df_plot_adj_filter.query('expression=="Unchanged"').sample(50000),
        df_plot_adj_filter.query('expression!="Unchanged"')
    ]
)

In [13]:
df_plot_adj_filter['-log10(FDR)'] = df_plot_adj_filter.padj.map(lambda x: -math.log10(x) if x != 0 else 0)
df_plot_adj_filter.dropna(axis=0, inplace=True)
df_plot_adj_filter

baseMean  log2FoldChange     lfcSE      stat  \
gene                                                                        
chr11_72750408_72754408    167.006440       -0.144270  0.771118  0.778949   
chr8_22040752_22044752      64.229580       -0.144270  0.415067  4.066236   
chr10_120948986_120949173   57.180016       -0.144270  0.378540 -0.437495   
chr3_23810225_23810649     120.468750       -0.144270  0.378540  1.579343   
chr2_108987220_108991220    78.305360       -0.144270  0.365100 -1.178582   
...                               ...             ...       ...       ...   
chr5_155011754_155015754    27.103321        1.115937  0.459624 -3.219578   
chr5_43395137_43399137      27.752563        1.329890  0.456962 -3.555297   
chr7_26358883_26362883      25.093758        1.214770  0.481852 -3.275733   
chr7_45025633_45029633      45.879845       -1.096671  0.358629  3.751380   
chrX_7841170_7845170        33.977050        1.322622  0.406804 -3.833647   

                             pvalue      padj  baseMean_lfc_shrink  \
gene                                                                 
chr11_72750408_72754408    0.436010  0.707481           167.006440   
chr8_22040752_22044752     0.000048  0.005458            64.229580   
chr10_120948986_120949173  0.661752  0.825898            57.180016   
chr3_23810225_23810649     0.114258  0.316485           120.468750   
chr2_108987220_108991220   0.238564  0.353263            78.305360   
...                             ...       ...                  ...   
chr5_155011754_155015754   0.001284  0.037198            27.103321   
chr5_43395137_43399137     0.000378  0.019646            27.752563   
chr7_26358883_26362883     0.001054  0.033792            25.093758   
chr7_45025633_45029633     0.000176  0.014516            45.879845   
chrX_7841170_7845170       0.000126  0.011438            33.977050   

                           log2FoldChange_lfc_shrink  lfcSE_lfc_shrink  \
gene                                                                     
chr11_72750408_72754408                    -0.144270          0.771118   
chr8_22040752_22044752                     -0.144270          0.415067   
chr10_120948986_120949173                  -0.144270          0.378540   
chr3_23810225_23810649                     -0.144270          0.378540   
chr2_108987220_108991220                   -0.144270          0.365100   
...                                              ...               ...   
chr5_155011754_155015754                    1.115937          0.459624   
chr5_43395137_43399137                      1.329890          0.456962   
chr7_26358883_26362883                      1.214770          0.481852   
chr7_45025633_45029633                     -1.096671          0.358629   
chrX_7841170_7845170                        1.322622          0.406804   

                           stat_lfc_shrink  pvalue_lfc_shrink  \
gene                                                            
chr11_72750408_72754408           0.778949           0.436010   
chr8_22040752_22044752            4.066236           0.000048   
chr10_120948986_120949173        -0.437495           0.661752   
chr3_23810225_23810649            1.579343           0.114258   
chr2_108987220_108991220         -1.178582           0.238564   
...                                    ...                ...   
chr5_155011754_155015754         -3.219578           0.001284   
chr5_43395137_43399137           -3.555297           0.000378   
chr7_26358883_26362883           -3.275733           0.001054   
chr7_45025633_45029633            3.751380           0.000176   
chrX_7841170_7845170             -3.833647           0.000126   

                           padj_lfc_shrink        region  \
gene                                                       
chr11_72750408_72754408           0.707481  tss_has_ctcf   
chr8_22040752_22044752            0.005458   tss_no_ctcf   
chr10_120948986_120949173         0.825898   CTCF_strong   
chr3_23

In [14]:
# df_plot_adj_filter['log2FoldChange'].describe()
# df_plot_adj_filter['-log10(FDR)'].describe()
# df_plot_adj_filter

In [15]:
from lets_plot import *
LetsPlot.setup_html()


g = (
    # 加N！！！
    ggplot(
        data=df_plot_adj_filter,
        mapping=aes(x='log2FoldChange', y='-log10(FDR)')
    )
    + geom_point(mapping=aes(color='expression'), size=1.5)
    + geom_vline(xintercept=fc_mt, size=0.4, color="black")
    + geom_vline(xintercept=fc_lt, size=0.4, color="black")
    + geom_hline(yintercept=FDR, size=0.4, color="black")
    + xlab('log2FC')
    + ylab('-log10FDR')
    + scale_x_continuous(limits=(-4.5, 4.5))
    + scale_y_continuous(limits=(0.0001, 10))
    + scale_color_manual(values = ["gray", "blue", "red"])
    + facet_grid(x='compare', y='region')
    + ggsize(width=4000, height=2500)
    + theme_bw()
)

g

In [ ]:
ggsave(g, filename='2023-05-25_ATAC-seq_VolcanoPlots_compare.html', path='.', iframe=True)

In [18]:
from lets_plot import *
LetsPlot.setup_html()


g = (
    # 加N！！！
    ggplot(
        data=(
            df_plot_adj_filter
            .query('compare!="log2(ND6_DddAwt_REP_1/SIRT6_DddA11_REP_1)"')
            .query('compare!="log2(ND6_DddAwt_REP_1/SIRT6_DddA11_REP_2)"')
            .query('compare!="log2(ND6_DddAwt_REP_2/SIRT6_DddA11_REP_1)"')
            .query('compare!="log2(ND6_DddAwt_REP_2/SIRT6_DddA11_REP_2)"')
            .query('compare!="log2(ND6_DddAwt_REP_1/ND6_DddAwt_REP_2)"')
            .query('compare!="log2(SIRT6_DddA11_REP_1/SIRT6_DddA11_REP_2)"')
            .query('compare!="log2(GFP_REP_1/ND6_DddAwt_REP_2)"')
            .query('region!="offs-ND6-DEP"')
            .query('region!="offs-ND6-IND"')
            .query('region!="CTCF_within-offs"')
            .query('region!="random"')
        ),
        mapping=aes(x='log2FoldChange', y='-log10(FDR)')
    )
    + geom_point(mapping=aes(color='expression'), size=1.5)
    + geom_vline(xintercept=fc_mt, size=0.4, color="black")
    + geom_vline(xintercept=fc_lt, size=0.4, color="black")
    + geom_hline(yintercept=FDR, size=0.4, color="black")
    + xlab('log2FC')
    + ylab('-log10FDR')
    + scale_x_continuous(limits=(-4.5, 4.5))
    + scale_y_continuous(limits=(0.0001, 10))
    + scale_color_manual(values = ["gray", "blue", "red"])
    + facet_grid(x='region', y='compare')
    + ggsize(width=2000, height=3000)
    + theme_bw()
)

g

In [ ]:
df_plot_adj_filter.query('expression=="Up-regulated"').index.str.split('_', expand=True).to_frame(index=None).drop_duplicates()

In [2]:
# pip install pyensembl
# https://github.com/openvax/pyensembl
# https://blog.csdn.net/jiangpeng59/article/details/83147236
# pyensembl -h
# pyensembl install --release 77 --species homo_sapiens
# release 77 use human reference genome GRCh38 (hg38)
import pyensembl as pe

# release 77 uses human reference genome GRCh38
data = pe.EnsemblRelease(77)

# will return ['HLA-A']
gene_names = data.gene_names_at_locus(contig=6, position=29945884)

# get all exons associated with HLA-A
exon_ids = data.exon_ids_of_gene_name('HLA-A')
print(exon_ids[:10])

gene_names = data.gene_names_at_locus(contig='1', position=100000, end=200000)
print(gene_names)

OperationalError: disk I/O error

In [ ]:
def get_gene_set_from_cps(df_cps, aim_cps_col, cp_direct='A2B'):
    """

    :param df_cps: df_cps dataframe
    :param aim_cps_col: 需要比较的列, 如cps_GFP_rep3_SIRT6-DddA11_Dead_rep1
    :param cp_direct:  A2B or B2A
    :return: gene_id list
    """
    set_cp = set()
    # print(f'{aim_cps_col}=="{cp_direct}"')

    for idx, row_info in df_cps.query(f'`{aim_cps_col}`=="{cp_direct}"')[['chrom', 'start', 'end']].iterrows():
        chrom, start, end = row_info
        chrom = chrom.replace('chr', '')
        # gene_names = data.gene_names_at_locus(contig=chrom, position=start, end=end)
        gene_objs = data.genes_at_locus(contig=chrom, position=start, end=end)
        gene_ids = [gene_obj.gene_id for gene_obj in gene_objs]
        # print(gene_ids)
        set_cp.update(gene_ids)
        ls_cp = sorted(list(set_cp))
    return ls_cp